In [189]:
import numpy as np
import matplotlib.pyplot as plt
import PIL

import torch
import torch.nn as nn
from torch import optim
import torch.nn.functional as F
from torch.autograd import Variable
use_cuda = torch.cuda.is_available()

In [190]:
GPU_NUM = 0 # 원하는 GPU 번호 입력
device = torch.device(f'cuda:{GPU_NUM}' if torch.cuda.is_available() else 'cpu')
torch.cuda.set_device(device) # change allocation of current GPU
print ('Current cuda device ', torch.cuda.current_device()) # check

# Additional Infos
if device.type == 'cuda':
    print(torch.cuda.get_device_name(GPU_NUM))
    print('Memory Usage:')
    print('Allocated:', round(torch.cuda.memory_allocated(GPU_NUM)/1024**3,1), 'GB')
    print('Cached:   ', round(torch.cuda.memory_cached(GPU_NUM)/1024**3,1), 'GB')

Current cuda device  0
GeForce GTX 1660 Ti
Memory Usage:
Allocated: 0.1 GB
Cached:    0.5 GB


C:\Users\Dustin Baek\.conda\envs\myenv\lib\site-packages\torch\cuda\memory.py:344: FutureWarning: torch.cuda.memory_cached has been renamed to torch.cuda.memory_reserved
  warnings.warn(


In [191]:
###################################### hyperparameters
class HParams():
    def __init__(self):
        self.data_location = 'cat.npz'
        self.enc_hidden_size = 256
        self.dec_hidden_size = 512
        self.Nz = 128
        self.M = 20
        self.dropout = 0.9
        self.batch_size = 100
        self.eta_min = 0.01
        self.R = 0.99995
        self.KL_min = 0.2
        self.wKL = 0.5
        self.lr = 0.001
        self.lr_decay = 0.9999
        self.min_lr = 0.00001
        self.grad_clip = 1.
        self.temperature = 0.4
        self.max_seq_length = 200

hp = HParams()

In [192]:
################################# load and prepare data
def max_size(data):
    """larger sequence length in the data set"""
    sizes = [len(seq) for seq in data]
#     len(seq)는 각 image의 row개수를 알려줌
# 그게 sequence (펜 움직인) 길이니까
# number of points
    return max(sizes)

def purify(strokes):
    """removes to small or too long sequences + removes large gaps"""
    data = []
    for seq in strokes:
#         70000개중 1개의 image가 seq이고, seq.shape[0]은 e.g. 51 (51x3)에서 나옴
        if seq.shape[0] <= hp.max_seq_length and seq.shape[0] > 10:
            seq = np.minimum(seq, 1000)
            seq = np.maximum(seq, -1000)
            seq = np.array(seq, dtype=np.float32)
            data.append(seq)
    return data

def calculate_normalizing_scale_factor(strokes):
    """Calculate the normalizing factor explained in appendix of sketch-rnn."""
    data = []
#     각 image의 x,y를 일렬로 쫙 data에 append. 총 len(data)는 70000 x 2 x (각 image의 row 개수)
    for i in range(len(strokes)):
        for j in range(len(strokes[i])):
            data.append(strokes[i][j, 0])
            data.append(strokes[i][j, 1])
    data = np.array(data)
    return np.std(data)

def normalize(strokes):
    """Normalize entire dataset (delta_x, delta_y) by the scaling factor."""
    data = []
    scale_factor = calculate_normalizing_scale_factor(strokes)
    for seq in strokes:
#         seq[:, 0:2]에서 첫번째 :이거는 모든 row를 다 포함시키겠다는거고
#         0:2는 그 row들의 첫번째 두번째 column을 indexing
        seq[:, 0:2] /= scale_factor
        data.append(seq)
    return data

In [193]:
data = []
for i in range(3):
    for j in range(4):
        data.append(4)
        data.append(1)
data = np.array(data)
print(np.std(data))

1.5


In [194]:
x = np.random.randn(5,5)
print(x)
print(x[:, 0:2])

[[-0.84288706 -0.81007502  0.23138612 -1.09344471  0.31905611]
 [-0.77993514 -0.48063765 -0.43322573 -0.85017802  1.23934203]
 [ 0.56073433 -0.16472515 -0.02395987 -0.70838435 -1.24048544]
 [-0.52897517 -1.55743127  0.53950104  0.70320162 -1.508241  ]
 [-0.35762015 -1.88266864  0.22042051 -0.85006095 -0.20699523]]
[[-0.84288706 -0.81007502]
 [-0.77993514 -0.48063765]
 [ 0.56073433 -0.16472515]
 [-0.52897517 -1.55743127]
 [-0.35762015 -1.88266864]]


In [195]:
x = np.random.randn(2,51,3)
print(x)
print("\n")
for i in x:
    print(i)
    print(i.shape[0])
    i = np.array(i, dtype=np.float32)
    print("\n")
    print(i)

[[[-2.10051127 -0.50021532 -0.29542511]
  [-0.77425718  0.33104448 -0.98908593]
  [-0.12055953 -0.24447894  1.00026517]
  [ 2.41124226 -1.35535783  0.85709503]
  [-0.52561922  1.57178625  0.16251373]
  [-0.06160139  0.60660753 -0.35287663]
  [-1.16274725  1.55443184 -0.11896821]
  [ 0.06108278  0.89401555  1.75379064]
  [-1.49949254 -1.40487934  0.0432748 ]
  [ 0.52984642 -1.28709861 -0.64841151]
  [-0.17892715 -1.639133   -0.44761373]
  [ 1.349245   -1.78496027 -0.25253838]
  [ 0.30086323  0.25019935  1.12035212]
  [ 0.84931648 -0.43235498  0.88208517]
  [ 1.17909964 -0.01538708 -0.50485062]
  [-0.70695009 -0.55172929  0.83845811]
  [ 0.97970715  0.32219204  0.4191813 ]
  [-0.27032153 -0.30811184  1.42830217]
  [ 1.27782949 -1.51466847 -1.5796183 ]
  [ 0.02296061  0.36609193  0.54293638]
  [ 0.09657662 -1.6435781   0.23927777]
  [-0.13816438 -0.69500382  0.04534715]
  [-0.3948403  -0.46959244  0.24788216]
  [-0.13672501  0.97554805 -0.36563871]
  [ 1.45266074  1.65725406  0.56381502]


In [196]:
dataset = np.load(hp.data_location, encoding='latin1', allow_pickle=True)
# print(dataset)
# print(dataset.keys())

data = dataset['train']
# for i in train_set:
#     print(train_set.shape)
print(len(data[1]))
#70000개의 channel, 각 channel이 한 image를뜻하고, 각 image는 2-d like 51x3

# calculate_normalizing_scale_factor(data)

valid_set = dataset['valid']
test_set = dataset['test']
# print(valid_set.shape)

data = purify(data)
# print(train_set)
data = normalize(data)
Nmax = max_size(data)
print(Nmax)

81
129


In [197]:
# import numpy as np
# # # save np.load
# # np_load_old = np.load
# np.load.__defaults__=(None, True, True, 'ASCII')

# # modify the default parameters of np.load
# # np.load = lambda *a,**k: np_load_old(*a, allow_pickle=True, **k)

# dataset = np.load(hp.data_location, encoding='latin1')

# data = dataset['train']
# data = purify(data)
# data = normalize(data)
# Nmax = max_size(data)
# # restore np.load for future normal usage
# # np.load = np_load_old
# np.load.__defaults__=(None, False, True, 'ASCII')
x=np.zeros((Nmax,5))
print(x.shape)

(129, 5)


In [198]:
############################## function to generate a batch:
def make_batch(batch_size):
    batch_idx = np.random.choice(len(data),batch_size)
#     batch_size개수만큼의 70000이하의 숫자들을 생성
    batch_sequences = [data[idx] for idx in batch_idx]
#     각 image의 2d array가 list로 저장, len(batch_sequences)=batch_size
    strokes = []
    lengths = []
    indice = 0
    for seq in batch_sequences:
        len_seq = len(seq[:,0])
        new_seq = np.zeros((Nmax,5))
        new_seq[:len_seq,:2] = seq[:,:2]
        new_seq[:len_seq-1,2] = 1-seq[:-1,2]
        new_seq[:len_seq,3] = seq[:,2]
        new_seq[(len_seq-1):,4] = 1
        new_seq[len_seq-1,2:4] = 0
        lengths.append(len(seq[:,0]))
        strokes.append(new_seq)
        indice += 1

#         np.stack(smt, 1)이면 row대로 (밑으로) 붙인다
    if use_cuda:
        batch = Variable(torch.from_numpy(np.stack(strokes,1)).cuda().float())
    else:
        batch = Variable(torch.from_numpy(np.stack(strokes,1)).float())
    return batch, lengths

In [199]:
################################ adaptive lr
def lr_decay(optimizer):
    """Decay learning rate by a factor of lr_decay"""
    for param_group in optimizer.param_groups:
        if param_group['lr']>hp.min_lr:
            param_group['lr'] *= hp.lr_decay
    return optimizer

In [200]:
a = torch.arange(10).reshape(1,5,2)
print(a)
print(torch.split(a,1))

tensor([[[0, 1],
         [2, 3],
         [4, 5],
         [6, 7],
         [8, 9]]])
(tensor([[[0, 1],
         [2, 3],
         [4, 5],
         [6, 7],
         [8, 9]]]),)


In [201]:
################################# encoder and decoder modules
class EncoderRNN(nn.Module):
    def __init__(self):
        super(EncoderRNN, self).__init__()
        # bidirectional lstm:
        self.lstm = nn.LSTM(5, hp.enc_hidden_size, \
            dropout=hp.dropout, bidirectional=True)
        # create mu and sigma from lstm's last output:
        self.fc_mu = nn.Linear(2*hp.enc_hidden_size, hp.Nz)
        self.fc_sigma = nn.Linear(2*hp.enc_hidden_size, hp.Nz)
        # active dropout:
        self.train()

    def forward(self, inputs, batch_size, hidden_cell=None):
        if hidden_cell is None:
            # then must init with zeros
            if use_cuda:
                hidden = torch.zeros(2, batch_size, hp.enc_hidden_size).cuda()
                cell = torch.zeros(2, batch_size, hp.enc_hidden_size).cuda()
            else:
                hidden = torch.zeros(2, batch_size, hp.enc_hidden_size)
                cell = torch.zeros(2, batch_size, hp.enc_hidden_size)
            hidden_cell = (hidden, cell)
        _, (hidden,cell) = self.lstm(inputs.float(), hidden_cell)
        # hidden is (2, batch_size, hidden_size), we want (batch_size, 2*hidden_size):
        hidden_forward, hidden_backward = torch.split(hidden,1,0)
        hidden_cat = torch.cat([hidden_forward.squeeze(0), hidden_backward.squeeze(0)],1)
        # mu and sigma:
        mu = self.fc_mu(hidden_cat)
        sigma_hat = self.fc_sigma(hidden_cat)
        sigma = torch.exp(sigma_hat/2.)
        # N ~ N(0,1)
        z_size = mu.size()
        if use_cuda:
            N = torch.normal(torch.zeros(z_size),torch.ones(z_size)).cuda()
        else:
            N = torch.normal(torch.zeros(z_size),torch.ones(z_size))
        z = mu + sigma*N
        # mu and sigma_hat are needed for LKL loss
        return z, mu, sigma_hat

In [202]:
x = torch.tensor([1, 2, 3, 4])
print(x.shape)
print(x.unsqueeze(0).shape)

torch.Size([4])
torch.Size([1, 4])


In [203]:
class DecoderRNN(nn.Module):
    def __init__(self):
        super(DecoderRNN, self).__init__()
        # to init hidden and cell from z:
        self.fc_hc = nn.Linear(hp.Nz, 2*hp.dec_hidden_size)
        # unidirectional lstm:
        self.lstm = nn.LSTM(hp.Nz+5, hp.dec_hidden_size, dropout=hp.dropout)
        # create proba distribution parameters from hiddens:
        self.fc_params = nn.Linear(hp.dec_hidden_size,6*hp.M+3)

    def forward(self, inputs, z, hidden_cell=None):
        if hidden_cell is None:
            # then we must init from z
            hidden,cell = torch.split(F.tanh(self.fc_hc(z)),hp.dec_hidden_size,1)
            hidden_cell = (hidden.unsqueeze(0).contiguous(), cell.unsqueeze(0).contiguous())
        outputs,(hidden,cell) = self.lstm(inputs, hidden_cell)
        # in training we feed the lstm with the whole input in one shot
        # and use all outputs contained in 'outputs', while in generate
        # mode we just feed with the last generated sample:
        if self.training:
            y = self.fc_params(outputs.view(-1, hp.dec_hidden_size))
        else:
            y = self.fc_params(hidden.view(-1, hp.dec_hidden_size))
        # separate pen and mixture params:
        params = torch.split(y,6,1)
        params_mixture = torch.stack(params[:-1]) # trajectory
        params_pen = params[-1] # pen up/down
        # identify mixture params:
        pi,mu_x,mu_y,sigma_x,sigma_y,rho_xy = torch.split(params_mixture,1,2)
        # preprocess params::
        if self.training:
            len_out = Nmax+1
        else:
            len_out = 1
                                   
        pi = F.softmax(pi.transpose(0,1).squeeze()).view(len_out,-1,hp.M)
        sigma_x = torch.exp(sigma_x.transpose(0,1).squeeze()).view(len_out,-1,hp.M)
        sigma_y = torch.exp(sigma_y.transpose(0,1).squeeze()).view(len_out,-1,hp.M)
        rho_xy = torch.tanh(rho_xy.transpose(0,1).squeeze()).view(len_out,-1,hp.M)
        mu_x = mu_x.transpose(0,1).squeeze().contiguous().view(len_out,-1,hp.M)
        mu_y = mu_y.transpose(0,1).squeeze().contiguous().view(len_out,-1,hp.M)
        q = F.softmax(params_pen).view(len_out,-1,3)
        return pi,mu_x,mu_y,sigma_x,sigma_y,rho_xy,q,hidden,cell

In [204]:
torch.stack([torch.Tensor([0,0,1,0,0])]*hp.batch_size)

tensor([[0., 0., 1., 0., 0.],
        [0., 0., 1., 0., 0.],
        [0., 0., 1., 0., 0.],
        [0., 0., 1., 0., 0.],
        [0., 0., 1., 0., 0.],
        [0., 0., 1., 0., 0.],
        [0., 0., 1., 0., 0.],
        [0., 0., 1., 0., 0.],
        [0., 0., 1., 0., 0.],
        [0., 0., 1., 0., 0.],
        [0., 0., 1., 0., 0.],
        [0., 0., 1., 0., 0.],
        [0., 0., 1., 0., 0.],
        [0., 0., 1., 0., 0.],
        [0., 0., 1., 0., 0.],
        [0., 0., 1., 0., 0.],
        [0., 0., 1., 0., 0.],
        [0., 0., 1., 0., 0.],
        [0., 0., 1., 0., 0.],
        [0., 0., 1., 0., 0.],
        [0., 0., 1., 0., 0.],
        [0., 0., 1., 0., 0.],
        [0., 0., 1., 0., 0.],
        [0., 0., 1., 0., 0.],
        [0., 0., 1., 0., 0.],
        [0., 0., 1., 0., 0.],
        [0., 0., 1., 0., 0.],
        [0., 0., 1., 0., 0.],
        [0., 0., 1., 0., 0.],
        [0., 0., 1., 0., 0.],
        [0., 0., 1., 0., 0.],
        [0., 0., 1., 0., 0.],
        [0., 0., 1., 0., 0.],
        [0

In [205]:
os = Variable(torch.Tensor([0,0,1,0,0]).view(1,1,-1))
print(os.shape)

torch.Size([1, 1, 5])


In [206]:
x = torch.ones(2,3,3)
idx = [2]
print(x.data[0,0,idx])


tensor([1.])


In [207]:
class Model():
    def __init__(self):
        if use_cuda:
            self.encoder = EncoderRNN().cuda()
            self.decoder = DecoderRNN().cuda()
        else:
            self.encoder = EncoderRNN()
            self.decoder = DecoderRNN()
        self.encoder_optimizer = optim.Adam(self.encoder.parameters(), hp.lr)
        self.decoder_optimizer = optim.Adam(self.decoder.parameters(), hp.lr)
        self.eta_step = hp.eta_min

    def make_target(self, batch, lengths):
        if use_cuda:
            eos = torch.stack([torch.Tensor([0,0,0,0,1])]*batch.size()[1]).cuda().unsqueeze(0)
        else:
            eos = torch.stack([torch.Tensor([0,0,0,0,1])]*batch.size()[1]).unsqueeze(0)
        batch = torch.cat([batch, eos], 0)
        mask = torch.zeros(Nmax+1, batch.size()[1])
        for indice,length in enumerate(lengths):
            mask[:length,indice] = 1
        if use_cuda:
            mask = mask.cuda()
        dx = torch.stack([batch.data[:,:,0]]*hp.M,2)
        dy = torch.stack([batch.data[:,:,1]]*hp.M,2)
        p1 = batch.data[:,:,2]
        p2 = batch.data[:,:,3]
        p3 = batch.data[:,:,4]
        p = torch.stack([p1,p2,p3],2)
        return mask,dx,dy,p

    def train(self, epoch):
        self.encoder.train()
        self.decoder.train()
        batch, lengths = make_batch(hp.batch_size)
        # encode:
#                                             input, batch_size
        z, self.mu, self.sigma = self.encoder(batch, hp.batch_size)
        # create start of sequence:
        if use_cuda:
            sos = torch.stack([torch.Tensor([0,0,1,0,0])]*hp.batch_size).cuda().unsqueeze(0)
        else:
            sos = torch.stack([torch.Tensor([0,0,1,0,0])]*hp.batch_size).unsqueeze(0)
        # had sos at the begining of the batch:
        batch_init = torch.cat([sos, batch],0)
        # expend z to be ready to concatenate with inputs:
        z_stack = torch.stack([z]*(Nmax+1))
        # inputs is concatenation of z and batch_inputs
        inputs = torch.cat([batch_init, z_stack],2)
        # decode:
        self.pi, self.mu_x, self.mu_y, self.sigma_x, self.sigma_y, \
            self.rho_xy, self.q, _, _ = self.decoder(inputs, z)
        # prepare targets:
        mask,dx,dy,p = self.make_target(batch, lengths)
        # prepare optimizers:
        self.encoder_optimizer.zero_grad()
        self.decoder_optimizer.zero_grad()
        # update eta for LKL:
        self.eta_step = 1-(1-hp.eta_min)*hp.R
        # compute losses:
        LKL = self.kullback_leibler_loss()
        LR = self.reconstruction_loss(mask,dx,dy,p,epoch)
        loss = LR + LKL
        # gradient step
        loss.backward()
        # gradient cliping
        nn.utils.clip_grad_norm(self.encoder.parameters(), hp.grad_clip)
        nn.utils.clip_grad_norm(self.decoder.parameters(), hp.grad_clip)
        # optim step
        self.encoder_optimizer.step()
        self.decoder_optimizer.step()
        # some print and save:
        if epoch%1==0:
#             import pdb; pdb.set_trace()
            print('epoch',epoch,'loss',loss.item(),'LR',LR.item(),'LKL',LKL.item())
#             print('epoch',epoch,'loss',loss.data[0],'LR',LR.data[0],'LKL',LKL.data[0])
            self.encoder_optimizer = lr_decay(self.encoder_optimizer)
            self.decoder_optimizer = lr_decay(self.decoder_optimizer)
        if epoch%100==0:
            #self.save(epoch)
            self.conditional_generation(epoch)
#             self.reconstruct()
    
    def bivariate_normal_pdf(self, dx, dy):
        z_x = ((dx-self.mu_x)/self.sigma_x)**2
        z_y = ((dy-self.mu_y)/self.sigma_y)**2
        z_xy = (dx-self.mu_x)*(dy-self.mu_y)/(self.sigma_x*self.sigma_y)
        z = z_x + z_y -2*self.rho_xy*z_xy
        exp = torch.exp(-z/(2*(1-self.rho_xy**2)))
        norm = 2*np.pi*self.sigma_x*self.sigma_y*torch.sqrt(1-self.rho_xy**2)
        return exp/norm

    def reconstruction_loss(self, mask, dx, dy, p, epoch):
        pdf = self.bivariate_normal_pdf(dx, dy)
        LS = -torch.sum(mask*torch.log(1e-5+torch.sum(self.pi * pdf, 2)))\
            /float(Nmax*hp.batch_size)
        LP = -torch.sum(p*torch.log(self.q))/float(Nmax*hp.batch_size)
        return LS+LP

    def kullback_leibler_loss(self):
        LKL = -0.5*torch.sum(1+self.sigma-self.mu**2-torch.exp(self.sigma))\
            /float(hp.Nz*hp.batch_size)
        if use_cuda:
            KL_min = Variable(torch.Tensor([hp.KL_min]).cuda()).detach()
        else:
            KL_min = Variable(torch.Tensor([hp.KL_min])).detach()
        return hp.wKL*self.eta_step * torch.max(LKL,KL_min)

    def save(self, epoch):
        sel = np.random.rand()
        torch.save(self.encoder.state_dict(), \
            'encoderRNN_sel_%3f_epoch_%d.pth' % (sel,epoch))
        torch.save(self.decoder.state_dict(), \
            'decoderRNN_sel_%3f_epoch_%d.pth' % (sel,epoch))

    def load(self, encoder_name, decoder_name):
        saved_encoder = torch.load(encoder_name)
        saved_decoder = torch.load(decoder_name)
        self.encoder.load_state_dict(saved_encoder)
        self.decoder.load_state_dict(saved_decoder)

    def conditional_generation(self, epoch):
        batch,lengths = make_batch(1)
        # should remove dropouts:
        self.encoder.train(False)
        self.decoder.train(False)
        # encode:
        z, _, _ = self.encoder(batch, 1)
        if use_cuda:
            sos = Variable(torch.Tensor([0,0,1,0,0]).view(1,1,-1).cuda())
        else:
            sos = Variable(torch.Tensor([0,0,1,0,0]).view(1,1,-1))
        s = sos
        seq_x = []
        seq_y = []
        seq_z = []
        hidden_cell = None
        for i in range(Nmax):
            input = torch.cat([s,z.unsqueeze(0)],2)
            # decode:
            self.pi, self.mu_x, self.mu_y, self.sigma_x, self.sigma_y, \
                self.rho_xy, self.q, hidden, cell = \
                    self.decoder(input, z, hidden_cell)
            hidden_cell = (hidden, cell)
            # sample from parameters:
            s, dx, dy, pen_down, eos = self.sample_next_state()
#             s, dx, dy, pen_down, eos = self.sample_next()

            #------
            seq_x.append(dx)
            seq_y.append(dy)
            seq_z.append(pen_down)
            if eos:
                print(i)
                break
        # visualize result:
        x_sample = np.cumsum(seq_x, 0)
        y_sample = np.cumsum(seq_y, 0)
        z_sample = np.array(seq_z)
        sequence = np.stack([x_sample,y_sample,z_sample]).T
        make_image(sequence, epoch)

    def sample_next(self, pi, mu_x, mu_y, sigma_x, sigma_y, rho_xy, q):
        pi, mu_x, mu_y, sigma_x, sigma_y, rho_xy, q =\
            pi[0, 0, :], mu_x[0, 0, :], mu_y[0, 0, :], sigma_x[0,
                                                               0, :], sigma_y[0, 0, :], rho_xy[0, 0, :], q[0, 0, :]
        mu_x, mu_y, sigma_x, sigma_y, rho_xy =\
            mu_x.cpu().numpy(), mu_y.cpu().numpy(), sigma_x.cpu(
            ).numpy(), sigma_y.cpu().numpy(), rho_xy.cpu().numpy()
        M = pi.shape[0]
        # offset
        idx = np.random.choice(M, p=pi.cpu().numpy())
        mean = [mu_x[idx], mu_y[idx]]
        cov = [[sigma_x[idx] * sigma_x[idx], rho_xy[idx] * sigma_x[idx]*sigma_y[idx]],
               [rho_xy[idx] * sigma_x[idx]*sigma_y[idx], sigma_y[idx] * sigma_y[idx]]]
        xy = np.random.multivariate_normal(mean, cov, 1)
        xy = torch.from_numpy(xy).float().to(device)

        # pen
        p = torch.tensor([0, 0, 0], device=device, dtype=torch.float)
        idx = np.random.choice(3, p=q.cpu().numpy())
        p[idx] = 1.0
        p = p.unsqueeze(0)

        return torch.cat([xy, p], dim=1).unsqueeze(0)
    
    def sample_next_state(self):

        def adjust_temp(pi_pdf):
            pi_pdf = np.log(pi_pdf)/hp.temperature
            pi_pdf -= pi_pdf.max()
            pi_pdf = np.exp(pi_pdf)
            pi_pdf /= pi_pdf.sum()
            return pi_pdf

        # get mixture indice:
        pi = self.pi.data[0,0,:].cpu().numpy()
        pi = adjust_temp(pi)
        pi_idx = np.random.choice(hp.M, p=pi)
        # get pen state:
        q = self.q.data[0,0,:].cpu().numpy()
        q = adjust_temp(q)
        q_idx = np.random.choice(3, p=q)
        # get mixture params:
#                                 len(pi_idx)가 들어가게됨
        mu_x = self.mu_x.data[0,0,pi_idx]
        mu_y = self.mu_y.data[0,0,pi_idx]
        sigma_x = self.sigma_x.data[0,0,pi_idx]
        sigma_y = self.sigma_y.data[0,0,pi_idx]
        rho_xy = self.rho_xy.data[0,0,pi_idx]
        
        mean = [mu_x, mu_y]
        mean = np.array([mu_x, mu_y], dtype=np.float64)
        sigma_x = sigma_x * np.sqrt(hp.temperature)
        sigma_y = sigma_y * np.sqrt(hp.temperature)
#         cov=[[1,1],[1,1]]
        cov = [[sigma_x * sigma_x, rho_xy * sigma_x * sigma_y],\
            [rho_xy * sigma_x * sigma_y, sigma_y * sigma_y]]
        cov = np.array([[sigma_x * sigma_x, rho_xy * sigma_x * sigma_y],[rho_xy * sigma_x * sigma_y, sigma_y * sigma_y]], dtype=np.float64)
        import pdb; pdb.set_trace
        xy = np.random.multivariate_normal(mean, cov, 1)
        x=xy[0][0] 
        y=xy[0][1] 
#         x,y = sample_bivariate_normal(mu_x,mu_y,sigma_x,sigma_y,rho_xy,greedy=False)
        next_state = torch.zeros(5)
        next_state[0] = x
        next_state[1] = y
        next_state[q_idx+2] = 1
        if use_cuda:
            return Variable(next_state.cuda()).view(1,1,-1),x,y,q_idx==1,q_idx==2
        else:
            return Variable(next_state).view(1,1,-1),x,y,q_idx==1,q_idx==2
#         return 1,2,3,4,5

# def sample_bivariate_normal(mu_x,mu_y,sigma_x,sigma_y,rho_xy, greedy=False):
#     # inputs must be floats
#     if greedy:
#         return mu_x,mu_y
#     mean = [mu_x, mu_y]
#     sigma_x = sigma_x * np.sqrt(hp.temperature)
#     sigma_y = sigma_y * np.sqrt(hp.temperature)
#     cov = [[sigma_x * sigma_x, rho_xy * sigma_x * sigma_y],\
#         [rho_xy * sigma_x * sigma_y, sigma_y * sigma_y]]
#     import pdb; pdb.set_trace
#     x = np.random.multivariate_normal(mean, cov, 1)
#     x = torch.from_numpy(xy).float().to(device)

#     return x[0][0], x[0][1]
    def reconstruct(self, S):
        self.encoder.eval()
        self.decoder.eval()
        with torch.no_grad():
            Nmax = S.shape[0]
            batch_size = S.shape[1]
            s_i = torch.stack(
                [torch.tensor([0, 0, 1, 0, 0], device=device, dtype=torch.float)] * batch_size, dim=0).unsqueeze(0)
            output = s_i  # dummy
            z, _, _ = self.encoder(S)
            h0, c0 = torch.split(torch.tanh(self.decoder.fc_hc(z)),
                                 self.decoder.dec_hidden_size, 1)
            hidden_cell = (h0.unsqueeze(0).contiguous(),
                           c0.unsqueeze(0).contiguous())
            for i in range(Nmax):
                (pi, mu_x, mu_y, sigma_x, sigma_y,
                 rho_xy, q), hidden_cell = self.decoder(s_i, z, hidden_cell)
                s_i = self.sample_next(
                    pi, mu_x, mu_y, sigma_x, sigma_y, rho_xy, q)
                output = torch.cat([output, s_i], dim=0)
                if output[-1, 0, 4] == 1:
                    break

            output = output[1:, :, :]  # remove dummy
            return output

    def sample_next(self, pi, mu_x, mu_y, sigma_x, sigma_y, rho_xy, q):
        pi, mu_x, mu_y, sigma_x, sigma_y, rho_xy, q =\
            pi[0, 0, :], mu_x[0, 0, :], mu_y[0, 0, :], sigma_x[0,
                                                               0, :], sigma_y[0, 0, :], rho_xy[0, 0, :], q[0, 0, :]
        mu_x, mu_y, sigma_x, sigma_y, rho_xy =\
            mu_x.cpu().numpy(), mu_y.cpu().numpy(), sigma_x.cpu(
            ).numpy(), sigma_y.cpu().numpy(), rho_xy.cpu().numpy()
        M = pi.shape[0]
        # offset
        idx = np.random.choice(M, p=pi.cpu().numpy())
        mean = [mu_x[idx], mu_y[idx]]
        cov = [[sigma_x[idx] * sigma_x[idx], rho_xy[idx] * sigma_x[idx]*sigma_y[idx]],
               [rho_xy[idx] * sigma_x[idx]*sigma_y[idx], sigma_y[idx] * sigma_y[idx]]]
        xy = np.random.multivariate_normal(mean, cov, 1)
        xy = torch.from_numpy(xy).float().to(device)

        # pen
        p = torch.tensor([0, 0, 0], device=device, dtype=torch.float)
        idx = np.random.choice(3, p=q.cpu().numpy())
        p[idx] = 1.0
        p = p.unsqueeze(0)

        return torch.cat([xy, p], dim=1).unsqueeze(0)


In [208]:
def make_image(sequence, epoch, name='_output_'):
    """plot drawing with separated strokes"""
    strokes = np.split(sequence, np.where(sequence[:,2]>0)[0]+1)
    fig = plt.figure()
    ax1 = fig.add_subplot(111)
    for s in strokes:
        plt.plot(s[:,0],-s[:,1])
    canvas = plt.get_current_fig_manager().canvas
    canvas.draw()
    pil_image = PIL.Image.frombytes('RGB', canvas.get_width_height(),
                 canvas.tostring_rgb())
    name = str(epoch)+name+'.jpg'
    pil_image.save(name,"JPEG")
    plt.close("all")

In [209]:
arrays = [np.random.randn(1, 1) for _ in range(10)]
print(arrays)

[array([[-0.51001199]]), array([[-1.32880626]]), array([[-0.79570227]]), array([[0.023427]]), array([[0.28846899]]), array([[-0.1577076]]), array([[0.05367381]]), array([[1.42525504]]), array([[-1.02237308]]), array([[-0.52167998]])]


In [210]:
x=np.random.randn(3,4)
print(x)
y=np.random.randn(3,4)
print(y)
np.stack([x,y])

[[-0.40716304 -1.46409236 -0.02488944  0.07599259]
 [ 1.65806582 -1.35603363 -1.10371984  1.18437166]
 [-0.73965437 -1.10535307  0.65729672 -0.0373229 ]]
[[-0.95683687  2.22552821  0.90234392 -1.03772584]
 [ 0.52092805  1.05588582  0.12533905  0.95103017]
 [-0.21520836 -0.6900452   1.02141197 -1.25694769]]


array([[[-0.40716304, -1.46409236, -0.02488944,  0.07599259],
        [ 1.65806582, -1.35603363, -1.10371984,  1.18437166],
        [-0.73965437, -1.10535307,  0.65729672, -0.0373229 ]],

       [[-0.95683687,  2.22552821,  0.90234392, -1.03772584],
        [ 0.52092805,  1.05588582,  0.12533905,  0.95103017],
        [-0.21520836, -0.6900452 ,  1.02141197, -1.25694769]]])

In [211]:
mean = [1, 2]
cov = [[1, 0], [0, 1]]  
x = np.random.multivariate_normal(mean, cov, 1)
print(x)
x = torch.from_numpy(x).float().to(device)
print(x.shape)

p = torch.tensor([0, 0, 0], device=device, dtype=torch.float)
idx = np.random.choice(3, 5)
print(idx)
p[idx] = 1.0
print(p)
p = p.unsqueeze(0)
print(p.shape)
z=torch.cat([x, p], dim=1).unsqueeze(0)
print(z.shape)
# print(x[0])
# print(x.shape)

[[2.82709951 2.35873629]]
torch.Size([1, 2])
[1 2 0 1 2]
tensor([1., 1., 1.], device='cuda:0')
torch.Size([1, 3])
torch.Size([1, 1, 5])


In [212]:
import numpy as np

b = np.zeros(1)
c = np.zeros(1)
c = c/2**63

b += c

In [213]:
model=Model()

C:\Users\Dustin Baek\.conda\envs\myenv\lib\site-packages\torch\nn\modules\rnn.py:58: UserWarning: dropout option adds dropout after all but last recurrent layer, so non-zero dropout expects num_layers greater than 1, but got dropout=0.9 and num_layers=1
  warnings.warn("dropout option adds dropout after all but last "


In [214]:
print("Model's state_dict:")
for param_tensor in model.state_dict():
    print(param_tensor, "\t", model.state_dict()[param_tensor].size())

Model's state_dict:


AttributeError: 'Model' object has no attribute 'state_dict'

In [215]:
model.encoder.state_dict()

OrderedDict([('lstm.weight_ih_l0',
              tensor([[ 6.1180e-02, -2.3263e-02,  3.4519e-02, -5.1125e-02,  2.1832e-02],
                      [-3.4036e-02, -2.0473e-03, -2.5708e-02,  2.9035e-02,  8.6183e-03],
                      [ 2.0172e-02, -1.3311e-02, -1.7053e-03,  5.2037e-02,  3.2584e-02],
                      ...,
                      [-5.6572e-02,  1.7812e-02,  5.5317e-02,  6.8635e-04, -1.1889e-02],
                      [-4.9143e-02, -2.5645e-05, -1.2556e-02, -2.2418e-02, -1.1055e-02],
                      [-3.2239e-02,  2.7249e-02, -2.8720e-02,  1.7094e-02,  5.5566e-02]],
                     device='cuda:0')),
             ('lstm.weight_hh_l0',
              tensor([[-0.0480,  0.0164,  0.0454,  ...,  0.0047, -0.0370,  0.0519],
                      [ 0.0460, -0.0259, -0.0150,  ...,  0.0167, -0.0238, -0.0143],
                      [-0.0565,  0.0078,  0.0478,  ...,  0.0414,  0.0349, -0.0567],
                      ...,
                      [ 0.0576, -0.0615, -0.0182,

In [216]:
if __name__=="__main__":
    model = Model()
    for epoch in range(50001):
        model.train(epoch)

<ipython-input-203-a948bd699ee2>:36: UserWarning: Implicit dimension choice for softmax has been deprecated. Change the call to include dim=X as an argument.
  pi = F.softmax(pi.transpose(0,1).squeeze()).view(len_out,-1,hp.M)
<ipython-input-203-a948bd699ee2>:42: UserWarning: Implicit dimension choice for softmax has been deprecated. Change the call to include dim=X as an argument.
  q = F.softmax(params_pen).view(len_out,-1,3)
<ipython-input-207-a50be1cf3273>:67: UserWarning: torch.nn.utils.clip_grad_norm is now deprecated in favor of torch.nn.utils.clip_grad_norm_.
  nn.utils.clip_grad_norm(self.encoder.parameters(), hp.grad_clip)
<ipython-input-207-a50be1cf3273>:68: UserWarning: torch.nn.utils.clip_grad_norm is now deprecated in favor of torch.nn.utils.clip_grad_norm_.
  nn.utils.clip_grad_norm(self.decoder.parameters(), hp.grad_clip)
C:\Users\Dustin Baek\.conda\envs\myenv\lib\site-packages\torch\nn\functional.py:1628: UserWarning: nn.functional.tanh is deprecated. Use torch.tanh ins

epoch 0 loss 2.419813394546509 LR 2.4188084602355957 LKL 0.0010049500269815326
1
epoch 1 loss 2.381244421005249 LR 2.380239486694336 LKL 0.0010049500269815326


<ipython-input-207-a50be1cf3273>:68: UserWarning: torch.nn.utils.clip_grad_norm is now deprecated in favor of torch.nn.utils.clip_grad_norm_.
  nn.utils.clip_grad_norm(self.decoder.parameters(), hp.grad_clip)


epoch 2 loss 2.497189521789551 LR 2.4961845874786377 LKL 0.0010049500269815326
epoch 3 loss 2.3125431537628174 LR 2.3115382194519043 LKL 0.0010049500269815326
epoch 4 loss 2.2314395904541016 LR 2.2304346561431885 LKL 0.0010049500269815326
epoch 5 loss 2.247342348098755 LR 2.246337413787842 LKL 0.0010049500269815326
epoch 6 loss 1.9871671199798584 LR 1.9861621856689453 LKL 0.0010049500269815326
epoch 7 loss 2.259406566619873 LR 2.25840163230896 LKL 0.0010049500269815326
epoch 8 loss 2.0399041175842285 LR 2.0388991832733154 LKL 0.0010049500269815326
epoch 9 loss 1.9737485647201538 LR 1.9727436304092407 LKL 0.0010049500269815326
epoch 10 loss 1.8675637245178223 LR 1.8665587902069092 LKL 0.0010049500269815326
epoch 11 loss 1.841461420059204 LR 1.840456485748291 LKL 0.0010049500269815326
epoch 12 loss 1.8234825134277344 LR 1.8224775791168213 LKL 0.0010049500269815326
epoch 13 loss 1.6655797958374023 LR 1.6645748615264893 LKL 0.0010049500269815326
epoch 14 loss 1.7003731727600098 LR 1.699368

C:\Users\Dustin Baek\.conda\envs\myenv\lib\site-packages\torch\nn\functional.py:1628: UserWarning: nn.functional.tanh is deprecated. Use torch.tanh instead.
  warnings.warn("nn.functional.tanh is deprecated. Use torch.tanh instead.")
<ipython-input-203-a948bd699ee2>:36: UserWarning: Implicit dimension choice for softmax has been deprecated. Change the call to include dim=X as an argument.
  pi = F.softmax(pi.transpose(0,1).squeeze()).view(len_out,-1,hp.M)
<ipython-input-203-a948bd699ee2>:42: UserWarning: Implicit dimension choice for softmax has been deprecated. Change the call to include dim=X as an argument.
  q = F.softmax(params_pen).view(len_out,-1,3)
<ipython-input-207-a50be1cf3273>:67: UserWarning: torch.nn.utils.clip_grad_norm is now deprecated in favor of torch.nn.utils.clip_grad_norm_.
  nn.utils.clip_grad_norm(self.encoder.parameters(), hp.grad_clip)
<ipython-input-207-a50be1cf3273>:68: UserWarning: torch.nn.utils.clip_grad_norm is now deprecated in favor of torch.nn.utils.c

...

epoch 49801 loss -0.44663095474243164 LR -0.48034894466400146 LKL 0.033717986196279526
epoch 49802 loss -0.4635687470436096 LR -0.4973106384277344 LKL 0.03374190255999565
epoch 49803 loss -0.3972683548927307 LR -0.43089210987091064 LKL 0.03362376242876053
epoch 49804 loss -0.4469848573207855 LR -0.4805446267127991 LKL 0.03355976566672325
epoch 49805 loss -0.4542991518974304 LR -0.48827075958251953 LKL 0.03397160768508911
epoch 49806 loss -0.45387566089630127 LR -0.48762696981430054 LKL 0.03375132009387016
epoch 49807 loss -0.47314321994781494 LR -0.5068097710609436 LKL 0.033666566014289856
epoch 49808 loss -0.4128991961479187 LR -0.44657760858535767 LKL 0.03367839753627777
epoch 49809 loss -0.44467857480049133 LR -0.478574275970459 LKL 0.03389570862054825
epoch 49810 loss -0.5038924813270569 LR -0.5377979278564453 LKL 0.033905431628227234
epoch 49811 loss -0.5015909075737 LR -0.5353348255157471 LKL 0.03374394029378891
epoch 49812 loss -0.44617900252342224 LR -0.4800277352333069 LKL 0.0

epoch 49900 loss -0.41923820972442627 LR -0.4528416097164154 LKL 0.03360338881611824
61


C:\Users\Dustin Baek\.conda\envs\myenv\lib\site-packages\torch\nn\functional.py:1628: UserWarning: nn.functional.tanh is deprecated. Use torch.tanh instead.
  warnings.warn("nn.functional.tanh is deprecated. Use torch.tanh instead.")
<ipython-input-203-a948bd699ee2>:36: UserWarning: Implicit dimension choice for softmax has been deprecated. Change the call to include dim=X as an argument.
  pi = F.softmax(pi.transpose(0,1).squeeze()).view(len_out,-1,hp.M)
<ipython-input-203-a948bd699ee2>:42: UserWarning: Implicit dimension choice for softmax has been deprecated. Change the call to include dim=X as an argument.
  q = F.softmax(params_pen).view(len_out,-1,3)
<ipython-input-207-a50be1cf3273>:67: UserWarning: torch.nn.utils.clip_grad_norm is now deprecated in favor of torch.nn.utils.clip_grad_norm_.
  nn.utils.clip_grad_norm(self.encoder.parameters(), hp.grad_clip)
<ipython-input-207-a50be1cf3273>:68: UserWarning: torch.nn.utils.clip_grad_norm is now deprecated in favor of torch.nn.utils.c

epoch 49901 loss -0.5244176387786865 LR -0.5584223866462708 LKL 0.034004777669906616
epoch 49902 loss -0.4436076581478119 LR -0.4774344563484192 LKL 0.0338268056511879
epoch 49903 loss -0.4476613402366638 LR -0.4813843071460724 LKL 0.033722952008247375
epoch 49904 loss -0.42076075077056885 LR -0.454571396112442 LKL 0.03381063789129257
epoch 49905 loss -0.4884796738624573 LR -0.5221737623214722 LKL 0.033694103360176086
epoch 49906 loss -0.4526996612548828 LR -0.4863950312137604 LKL 0.03369535505771637
epoch 49907 loss -0.43051058053970337 LR -0.46429088711738586 LKL 0.03378032147884369
epoch 49908 loss -0.39591073989868164 LR -0.42952919006347656 LKL 0.03361843526363373
epoch 49909 loss -0.4558570683002472 LR -0.48976564407348633 LKL 0.03390856459736824
epoch 49910 loss -0.43187782168388367 LR -0.4654976427555084 LKL 0.03361980989575386
epoch 49911 loss -0.4777476489543915 LR -0.5115693211555481 LKL 0.03382168337702751
epoch 49912 loss -0.48154935240745544 LR -0.5155132412910461 LKL 0.0

epoch 49999 loss -0.4561496078968048 LR -0.4897915720939636 LKL 0.033641964197158813
epoch 50000 loss -0.4569929242134094 LR -0.49086010456085205 LKL 0.03386716917157173
46
